Ресурсы, где был подсмотрен код или подход

https://towardsdatascience.com/retrieving-openstreetmap-data-in-python-1777a4be45bb

https://geopandas.org/en/stable/


https://github.com/datasouls/mts-geohack/blob/master/Geohack112_StarterKit.ipynb

https://habr.com/ru/post/579838/

https://towardsdatascience.com/how-to-find-best-locations-for-your-restaurants-with-python-b2fadc91c4dd

# Поиск потенциальных мест для открытия пвз в Ульяновске (своя тема)

# Установка и импорт библиотек

In [ ]:
!pip install geopandas
!pip install h3
!pip install osmnx
!pip install folium
!pip install fast-pagerank

/usr/local/lib/python3.7/dist-packages/google/colab/_pip.py:87: ResourceWarning: unclosed file <_io.TextIOWrapper name='/usr/local/lib/python3.7/dist-packages/fast_pagerank-0.0.4.dist-info/top_level.txt' mode='r' encoding='UTF-8'>
  for line in open(toplevel):


In [ ]:
import geopandas as gpd
import pandas as pd
import numpy as np
import json
import h3
import folium
import osmnx as ox
from shapely import wkt
from folium.plugins import HeatMap
from shapely.geometry import Polygon
from scipy import sparse
from fast_pagerank import pagerank
import torch

# Исследование и отображение доступных данных
Библиотека [H3](https://eng.uber.com/h3/) позволяет поделить карту на гексагоны, а библиотека [folium](https://python-visualization.github.io/folium/) позволяет отображать различные данные на карте города.

In [ ]:
def visualize_hexagons(hexagons, color="red", folium_map=None):

    polylines = []
    lat = []
    lng = []
    for hex in hexagons:
        polygons = h3.h3_set_to_multi_polygon([hex], geo_json=False)
        outlines = [loop for polygon in polygons for loop in polygon]
        polyline = [outline + [outline[0]] for outline in outlines][0]
        lat.extend(map(lambda v:v[0],polyline))
        lng.extend(map(lambda v:v[1],polyline))
        polylines.append(polyline)
    
    if folium_map is None:
        m = folium.Map(location=[sum(lat)/len(lat), sum(lng)/len(lng)], zoom_start=20, tiles='cartodbpositron')
    else:
        m = folium_map
        
    for polyline in polylines:
        my_PolyLine=folium.PolyLine(locations=polyline,weight=8,color=color)
        m.add_child(my_PolyLine)
    return m
  

LAT_MIN, LAT_MAX = 54.1709, 54.4449
LON_MIN, LON_MAX = 48.0810, 48.8953

h3_address = h3.geo_to_h3(54.3, 48.4,  9) # 9 - индекс, определяющий размер гексагона                                                                                                     
visualize_hexagons([h3_address])

Проект [OpenStreetMap](https://ru.wikipedia.org/wiki/OpenStreetMap) собирает различные геоданные. Отсюда можно взять данные о различных объектах в городе Ульяновске. [Здесь](https://wiki.openstreetmap.org/wiki/RU:%D0%9E%D0%B1%D1%8A%D0%B5%D0%BA%D1%82%D1%8B_%D0%BA%D0%B0%D1%80%D1%82%D1%8B) есть описание всех таких объектов.

In [ ]:
def visualize_polygons(geometry):
    
    lats, lons = get_lat_lon(geometry)
    
    m = folium.Map(location=[sum(lats)/len(lats), sum(lons)/len(lons)], zoom_start=13, tiles='cartodbpositron')
    
    overlay = gpd.GeoSeries(geometry).to_json()
    folium.GeoJson(overlay, name = 'boundary').add_to(m)
    
    return m

# выводим центроиды полигонов
def get_lat_lon(geometry):
        
    lon = geometry.apply(lambda x: x.x if x.type == 'Point' else x.centroid.x)
    lat = geometry.apply(lambda x: x.y if x.type == 'Point' else x.centroid.y)
    return lat, lon
  
# выгрузим границы Ульяновска из OSM
cities = ['Ульяновск']
polygon_krd = ox.geometries_from_place(cities, {'boundary':'administrative'}).reset_index()
polygon_krd = polygon_krd[(polygon_krd['name'] == 'городской округ Ульяновск')]
# посмотрим что получилось
visualize_polygons(polygon_krd['geometry'])

Поделим город на гексагоны

In [ ]:
def create_hexagons(geoJson):
    
    polyline = geoJson['coordinates'][0]

    polyline.append(polyline[0])
    lat = [p[0] for p in polyline]
    lng = [p[1] for p in polyline]
    m = folium.Map(location=[sum(lat)/len(lat), sum(lng)/len(lng)], zoom_start=13, tiles='cartodbpositron')
    my_PolyLine=folium.PolyLine(locations=polyline,weight=8,color="green")
    m.add_child(my_PolyLine)

    hexagons = list(h3.polyfill(geoJson, 8))
    polylines = []
    lat = []
    lng = []
    for hex in hexagons:
        polygons = h3.h3_set_to_multi_polygon([hex], geo_json=False)
        # flatten polygons into loops.
        outlines = [loop for polygon in polygons for loop in polygon]
        polyline = [outline + [outline[0]] for outline in outlines][0]
        lat.extend(map(lambda v:v[0],polyline))
        lng.extend(map(lambda v:v[1],polyline))
        polylines.append(polyline)
    for polyline in polylines:
        my_PolyLine=folium.PolyLine(locations=polyline,weight=3,color='red')
        m.add_child(my_PolyLine)
        
    polylines_x = []
    for j in range(len(polylines)):
        a = np.column_stack((np.array(polylines[j])[:,1],np.array(polylines[j])[:,0])).tolist()
        polylines_x.append([(a[i][0], a[i][1]) for i in range(len(a))])
        
    polygons_hex = pd.Series(polylines_x).apply(lambda x: Polygon(x))
        
    return m, polygons_hex, polylines
# polygon_hex , polylines - геометрии гексагонов в разных форматах

# сгенерим гексагоны внутри полигона г. Ульяновск
geoJson = json.loads(gpd.GeoSeries(polygon_krd['geometry']).to_json())
geoJson = geoJson['features'][0]['geometry']
geoJson = {'type':'Polygon','coordinates': [np.column_stack((np.array(geoJson['coordinates'][0])[:, 1],
                                                      np.array(geoJson['coordinates'][0])[:, 0])).tolist()]}

m, polygons, polylines = create_hexagons(geoJson)
m

Выгрузим с OSM данные о различных постройках.

In [ ]:
def osm_query(tag, city):
    gdf = ox.geometries_from_place(city, tag).reset_index()
    gdf['city'] = np.full(len(gdf), city.split(',')[0])
    gdf['object'] = np.full(len(gdf), list(tag.keys())[0])
    gdf['type'] = np.full(len(gdf), tag[list(tag.keys())[0]])
    gdf['area'] = gdf.to_crs({'proj':'cea'})['geometry'].area
    gdf = gdf[['city', 'object', 'type', 'geometry', 'area']]
    print(gdf.shape)
    return gdf
  
 # Выгрузим интересующие нас категории объектов 
tags = [
        {'building' : 'apartments'}, {'building' : 'detached'}, 
        {'building' : 'dormitory'}, {'building' : 'hotel'}, 
        {'building' : 'house'}, {'building' : 'semidetached_house'}, 
        {'building' : 'terrace'},  {'building' : 'commercial'},
        {'building' : 'office'}, {'building':'retail'}, 
        {'building':'train_station'},
        {'highway' : 'bus_stop'}, {'footway':'crossing'},
        {'amenity':'cafe'}, {'amenity':'fast_food'}, 
        {'amenity':'restaurant'}, {'amenity':'college'}, 
        {'amenity':'language_school'},  {'amenity':'school'},  
        {'amenity':'university'},  {'amenity':'atm'},  
        {'amenity':'bank'},  {'amenity':'clinic'},  
        {'amenity':'hospital'},  {'amenity':'pharmacy'},  
        {'amenity':'theatre'},  {'amenity':'townhall'},  
        {'amenity':'bench'},
        {'shop':'outpost'}
       ]
cities = ['Ульяновск, Россия']

gdfs = []
for city in cities:
    for tag in tags:
        gdfs.append(osm_query(tag, city))
        
# посмотрим что получилось
data_poi = pd.concat(gdfs)
data_poi.groupby(['city','object','type'], as_index = False).agg({'geometry':'count'})

# добавим координаты/центроиды
lat, lon = get_lat_lon(data_poi['geometry'])
data_poi['lat'] = lat
data_poi['lon'] = lon

/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):


(2864, 5)
(127, 5)
(16, 5)
(21, 5)
(4019, 5)
(2, 5)
(1, 5)
(210, 5)
(70, 5)
(255, 5)
(5, 5)
(677, 5)
(670, 5)
(260, 5)
(79, 5)
(55, 5)
(23, 5)
(1, 5)
(103, 5)
(16, 5)
(141, 5)
(92, 5)
(47, 5)
(40, 5)
(229, 5)
(5, 5)
(1, 5)
(1106, 5)
(70, 5)


In [ ]:
# sjoin - spatial join - пересекаем гексагоны с объектами (определяем какие объекты находятся в разрезе каждого гексагона)

gdf_1 = gpd.GeoDataFrame(data_poi, geometry=gpd.points_from_xy(data_poi.lon, data_poi.lat))

gdf_2 = pd.DataFrame(polygons, columns = ['geometry'])
gdf_2['polylines'] = polylines
gdf_2['geometry'] = gdf_2['geometry'].astype(str)
geometry_uniq = pd.DataFrame(gdf_2['geometry'].drop_duplicates())
geometry_uniq['id'] = np.arange(len(geometry_uniq)).astype(str)
gdf_2 = gdf_2.merge(geometry_uniq, on = 'geometry')
gdf_2['geometry'] = gdf_2['geometry'].apply(wkt.loads)
gdf_2 = gpd.GeoDataFrame(gdf_2, geometry='geometry')

itog_table = gpd.sjoin(gdf_2, gdf_1, how='left', op='intersects')
itog_table = itog_table.dropna()
itog_table.head()

/usr/local/lib/python3.7/dist-packages/IPython/core/interactiveshell.py:2822: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  if self.run_code(code, result):


geometry  ...        lon
0  POLYGON ((48.33611 54.26022, 48.33258 54.26470...  ...  48.332178
0  POLYGON ((48.33611 54.26022, 48.33258 54.26470...  ...  48.331516
0  POLYGON ((48.33611 54.26022, 48.33258 54.26470...  ...  48.328656
0  POLYGON ((48.33611 54.26022, 48.33258 54.26470...  ...  48.325646
0  POLYGON ((48.33611 54.26022, 48.33258 54.26470...  ...  48.326406

[5 rows x 10 columns]

## Плотность размещения существующих пунктов выдачи заказов

ПВЗ представлены тегом shop:outpost. Посчитаем количество ПВЗ для разных гексагонов и отобразим на карте.

In [ ]:
def create_choropleth(data, json, columns, legend_name, feature, bins):
    
    lat, lon = get_lat_lon(data['geometry'])

    m = folium.Map(location=[sum(lat)/len(lat), sum(lon)/len(lon)], zoom_start=13, tiles='cartodbpositron')
    
    folium.Choropleth(
        geo_data=json,
        name="choropleth",
        data=data,
        columns=columns,
        key_on="feature.id",
        fill_color="YlGn",
        fill_opacity=0.7,
        line_opacity=0.2,
        legend_name=legend_name,
        nan_fill_color = 'black',
        bins = bins

    ).add_to(m)

    folium.LayerControl().add_to(m)

    return m
  
# подготовим данные 
itog_table['geometry'] = itog_table['geometry'].astype(str) #для groupby
itog_table['id'] = itog_table['id'].astype(str) #для Choropleth
agg_all = itog_table.groupby(['geometry','type','id'], as_index = False).agg({'lat':'count'}).rename(columns = {'lat':'counts'})
agg_all['geometry'] = agg_all['geometry'].apply(wkt.loads) #возвращаем формат геометрий

agg_all_outposts = agg_all.query("type == 'outpost'")[["geometry","counts",'id']]
agg_all_outposts['id'] = agg_all_outposts['id'].astype(str)
data_geo_1 = gpd.GeoSeries(agg_all_outposts.set_index('id')["geometry"]).to_json()

create_choropleth(agg_all_outposts, data_geo_1, ["id","counts"], 'Outpost counts', 'counts', 5)

/usr/local/lib/python3.7/dist-packages/geopandas/geodataframe.py:1350: UserWarning: Geometry column does not contain geometry.
  warnings.warn("Geometry column does not contain geometry.")


Посмотрим на полноту данных об этажах и номерах квартир для жилых зданий, то есть отношение данных без пропусков ко всем данным. 

In [ ]:
gdf_aparts = ox.geometries_from_place(city, {'building' : 'apartments'}).reset_index()
# полнота building:levels (этажи)
print(np.round(len(gdf_aparts['building:levels'].dropna())/len(gdf_aparts['building:levels']), 2))

# полнота building:flats (квартиры)
print(np.round(len(gdf_aparts['building:flats'].dropna())/len(gdf_aparts['building:flats']), 2))

/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
/usr/local/lib/python3.7/dist-packages/osmnx/geometries.py:805: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):


0.96
0.05


## Отображение плотности людей через их дома

Вычислим плотность населения, условимся, что в среднем в квартире проживает семья из 3 человек, а на этаже 10 квартир.

In [ ]:
# добавим фичу - население

lat_g, lon_g = get_lat_lon(gdf_aparts['geometry'])
gdf_aparts['lat'] = lat_g
gdf_aparts['lon'] = lon_g

itog_table_people = itog_table.merge(gdf_aparts[['lat', 'lon', 'building:levels']], on = ['lat', 'lon'], how = 'left')
itog_table_people['building:levels'] = itog_table_people['building:levels'].fillna(1)
itog_table_people = itog_table_people.rename(columns = {'building:levels' : 'levels'})

apartments = ['apartments' , 'dormitory']
houses = ['house', 'semidetached_house', 'detached', 'terrace']
people_ctn = []

# в среднем возьмем 3 чел. на семью

for i in range(len(itog_table_people)):
    
    if itog_table_people['type'].iloc[i] in apartments:
        
        people = int(itog_table_people['levels'].iloc[i])*10*3
        
    elif itog_table_people['type'].iloc[i] in houses:
        
        people = int(itog_table_people['levels'].iloc[i])*3
        
    else:
        people = 'not living area'
        
    people_ctn.append(people)
    
itog_table_people['count_people'] = people_ctn

table_people = itog_table_people.query("count_people != 'not living area'")
table_people['count_people'] = table_people['count_people'].astype(int)

/usr/local/lib/python3.7/dist-packages/geopandas/geodataframe.py:1351: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


In [ ]:
def create_choropleth_and_heatmap(data, json, columns, legend_name, feature, bins, heat_data, lat_lon_feature):

    lat, lon = get_lat_lon(data['geometry'])

    m = folium.Map(location=[sum(lat)/len(lat), sum(lon)/len(lon)], zoom_start=13, tiles='cartodbpositron')

    folium.Choropleth(
        geo_data=json,
        name="choropleth",
        data=data,
        columns=columns,
        key_on="feature.id",
        fill_color="YlGn",
        fill_opacity=0.7,
        line_opacity=0.2,
        legend_name=legend_name,
        nan_fill_color = 'black',
        bins = bins

    ).add_to(m)

    HeatMap(heat_data[lat_lon_feature].groupby(lat_lon_feature[0:2]).sum().reset_index().values.tolist(),
            radius = 70, min_opacity = 0.05, max_val = int((heat_data[lat_lon_feature[2]]).quantile([0.75])), name='heatmap', blur=30).add_to(m)
    
    folium.LayerControl().add_to(m)

    return m
  
# карта плотности населения
create_choropleth_and_heatmap(agg_all_outposts, data_geo_1, ["id","counts"], 'Outpost counts', 'counts', 5, table_people, ['lat', 'lon', 'count_people'])

## Отображение плотности людей через офисы

В среднем будем считать, что на 40 квадратных метров офиса приходится 10 офисных работников.

In [ ]:
offices = ['office' , 'commercial']
worker_ctn = []

for i in range(len(itog_table)):
    
    if itog_table['type'].iloc[i] in offices:
        
        workers = int(itog_table['area'].iloc[i]) / 40 * 10
        
    else:
        workers = 'not working area'
        
    worker_ctn.append(workers)
    
itog_table['count_workers'] = worker_ctn

table_workers = itog_table.query("count_workers != 'not working area'")
table_workers['count_workers'] = table_workers['count_workers'].astype(int)

/usr/local/lib/python3.7/dist-packages/geopandas/geodataframe.py:1351: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


In [ ]:
create_choropleth_and_heatmap(agg_all_outposts, data_geo_1, ["id","counts"], 'Outpost counts', 'counts', 5, table_workers, ['lat', 'lon', 'count_workers'])

# Генерация фич и датасета
Сгенерируем следующие фичи для гексагонов: количество ПВЗ, количество людей и количество работников, а также метрику, учитывающую эти фичи.

Метрика = (Кол-во людей + кол-во работников) / (Кол-во ПВЗ + 1)

К знаменателю прибавляем единицу, чтобы избежать деления на ноль.

In [ ]:
hex_features = itog_table[['id', 'lat', 'lon']].groupby('id', as_index=False).mean()

dfhelper = itog_table[itog_table['type'] == 'outpost'].groupby('id')['type'].count()
hex_features = hex_features.set_index('id').join(dfhelper).reset_index()

dfhelper = table_people.groupby('id')['count_people'].sum()
hex_features = hex_features.set_index('id').join(dfhelper).reset_index()

dfhelper = table_workers.groupby('id')['count_workers'].sum()
hex_features = hex_features.set_index('id').join(dfhelper).reset_index()

hex_features.rename(columns = {'type':'outpost_count'}, inplace = True)
hex_features = hex_features.fillna(0)

metric = lambda row: (row['count_people'] + row['count_workers']) / (row['outpost_count'] + 1)

hex_features['metric'] = hex_features.apply(metric, axis=1)

hex_features

id        lat        lon  ...  count_people  count_workers   metric
0      0  54.261421  48.327273  ...       13611.0            0.0  3402.75
1    101  54.377039  48.581851  ...        8280.0          446.0  1745.20
2    105  54.245122  48.329043  ...           0.0            0.0     0.00
3    108  54.326833  48.483835  ...        2190.0          268.0  2458.00
4    112  54.315144  48.372995  ...        3840.0          119.0  3959.00
..   ...        ...        ...  ...           ...            ...      ...
179    9  54.248346  48.308989  ...         324.0            0.0   324.00
180   92  54.235485  48.303445  ...          33.0          575.0   608.00
181   97  54.251670  48.287003  ...         111.0            0.0   111.00
182   98  54.348863  48.379078  ...        3195.0            0.0  1597.50
183   99  54.270207  48.302868  ...        8490.0          922.0  4706.00

[184 rows x 7 columns]

In [ ]:
hex_features[['count_people', 'count_workers']].corr()

count_people  count_workers
count_people       1.000000       0.277986
count_workers      0.277986       1.000000

# О задаче

Задача состоит в нахождении потенциальных мест для ПВЗ, где высокая плотность людей и минимум других ПВЗ.

Задачу можно свести к задаче выбора лучшей вершины в графе. Она может решаться как обучение с учителем или обучение без учителя. Обучение с учителем - это с использованием графовых нейронных сетей, без учителя - PageRank и модификация Personalized PageRank (возможно есть другие методы).

|#  | Метод                         | Необходимость в таргете  |
|:-:|-------------------------------|:------------------------:|
|1  | Выбрать топ по метрике        | **Нет**                  |
|2  | PageRank                      | **Нет**                  |
|3  | Personalized PageRank         | **Нет**                  |
|3  | Графовые нейронные сетки      |  Есть                    |

На основе анализа существующих методов и того, что таргета в датасете нет, то выбор был сделан в сторону методов 1, 2 и 3.

# Бейзлайн
Отсортируем гексагоны по метрике, найдем 10 с самым большим значением

In [ ]:
best_hex = hex_features.sort_values('metric', ascending=False).head(10)
best_ids_1 = best_hex.id.tolist()
best_hex

id        lat        lon  ...  count_people  count_workers   metric
67   371  54.348240  48.338453  ...       12906.0            0.0  12906.0
11   168  54.345053  48.388075  ...       10407.0          364.0  10771.0
46   290  54.300144  48.319936  ...        9384.0          252.0   9636.0
29    23  54.320189  48.386178  ...        7557.0         1561.0   9118.0
138   68  54.311917  48.358385  ...        8460.0            0.0   8460.0
175  821  54.268726  48.326872  ...        7647.0           78.0   7725.0
143  700  54.340138  48.396721  ...        5895.0         1741.0   7636.0
168  787  54.369434  48.582745  ...        9960.0         5200.0   7580.0
178   85  54.283132  48.293655  ...       14100.0            0.0   7050.0
92   478  54.277111  48.270168  ...        6828.0            0.0   6828.0

[10 rows x 7 columns]

## Отображение потенциальных мест для открытия ПВЗ
Шкала отображает предпочтение гексагонов, чем оно выше, тем предпочтительный гексагон.

In [ ]:
agg_all = agg_all.merge(hex_features[['id', 'metric']], how='left', on='id')
potential_outposts = agg_all[agg_all.id.isin(best_ids_1)]

data_geo_1 = gpd.GeoSeries(potential_outposts.set_index('id')["geometry"]).to_json()

create_choropleth_and_heatmap(potential_outposts, data_geo_1, ["id","metric"], 'Outpost', 'counts', 3, table_people, ['lat', 'lon', 'count_people'])

In [ ]:
create_choropleth_and_heatmap(potential_outposts, data_geo_1, ["id","metric"], 'Outpost', 'counts', 3, table_workers, ['lat', 'lon', 'count_workers'])

# Метод PageRank
Для того, чтобы учесть информацию о соседних гексагонов, можно воспользоваться методом PageRank. Для него нужно создать матрицу переходов между различными состояними. Состояними будем считать разные гексагоны, а переход между состоянием i и j возможно только в случае, если метрика для i гексагона меньше, чем для j гексагона.

Результат метода - это такие вершины, у которых среди соседей больше всего "важных" вершин, то есть таких, которые имеют больше переходов в себя.

In [ ]:
# https://gist.github.com/diogojc/1338222/84d767a68da711a154778fb1d00e772d65322187

import numpy as np
from scipy.sparse import csc_matrix

def pageRank(G, s = .85, maxerr = .0001):
    """
    Computes the pagerank for each of the n states
    Parameters
    ----------
    G: matrix representing state transitions
       Gij is a binary value representing a transition from state i to j.
    s: probability of following a transition. 1-s probability of teleporting
       to another state.
    maxerr: if the sum of pageranks between iterations is bellow this we will
            have converged.
    """
    n = G.shape[0]

    # transform G into markov matrix A
    A = csc_matrix(G,dtype=float)
    rsums = np.array(A.sum(1))[:,0]
    ri, ci = A.nonzero()
    A.data /= rsums[ri]

    # bool array of sink states
    sink = rsums==0

    # Compute pagerank r until we converge
    ro, r = np.zeros(n), np.ones(n)
    while np.sum(np.abs(r-ro)) > maxerr:
        ro = r.copy()
        # calculate each pagerank at a time
        for i in range(n):
            # inlinks of state i
            Ai = np.array(A[:,i].todense())[:,0]
            # account for sink states
            Di = sink / float(n)
            # account for teleportation to state i
            Ei = np.ones(n) / float(n)

            r[i] = ro.dot( Ai*s + Di*s + Ei*(1-s) )

    # return normalized pagerank
    return r/float(sum(r))

## Генерация матрицы переходов

In [ ]:
a = []

def get_hex_id(row):
    return h3.geo_to_h3(row['lat'], row['lon'], 8)

ids = {}
for idx, row in hex_features.iterrows():
    ids[row['id']] = get_hex_id(row)

for idx, row in hex_features.iterrows():
    line = []
    for idx2, row2 in hex_features.iterrows():
        are_neigh = h3.h3_indexes_are_neighbors(ids[row['id']], ids[row2['id']])
        line.append(int(are_neigh and (row['metric'] < row2['metric'])))
    a.append(line)

a = np.array(a)

## Вычисление рангов гексагонов и нахождение индексов лучших из них

In [ ]:
ranks = pageRank(a)
hex_features['ranks'] = ranks
indices = ranks.argsort()[-10:]
best_ids_2 = np.take(hex_features.id.tolist(), indices)
print(best_ids_2)
print(ranks[indices])

['722' '819' '726' '45' '835' '821' '762' '750' '23' '578']
[0.01361602 0.01394391 0.01426162 0.01531289 0.01539821 0.01641779
 0.01783469 0.01811912 0.02084882 0.02469439]


В таблице отображены гексагоны с самыми лучшими значениями в столбце ranks

In [ ]:
hex_features[hex_features.id.isin(best_ids)]

id        lat        lon  ...  metric     ranks  personalized_ranks
29    23  54.320189  48.386178  ...  9118.0  0.020849            0.012106
87    45  54.349227  48.540387  ...  4903.0  0.015313            0.005813
117  578  54.347297  48.366767  ...  5757.0  0.024694            0.008956
148  722  54.383198  48.570295  ...  4260.0  0.013616            0.008937
150  726  54.320342  48.361146  ...  3599.5  0.014262            0.007736
158  750  54.337496  48.365953  ...  1691.0  0.018119            0.006772
161  762  54.341816  48.377882  ...  4222.0  0.017835            0.010120
174  819  54.353738  48.531222  ...  2655.5  0.013944            0.004263
175  821  54.268726  48.326872  ...  7725.0  0.016418            0.009353
177  835  54.328238  48.388330  ...  3914.0  0.015398            0.010544

[10 rows x 9 columns]

## Отображение потенциальных мест для открытия ПВЗ
Шкала отображает предпочтение гексагонов, чем оно выше, тем предпочтительный гексагон.

In [ ]:
agg_all = agg_all.merge(hex_features[['id', 'ranks']], how='left', on='id')
potential_outposts = agg_all[agg_all.id.isin(best_ids_2)]

data_geo_1 = gpd.GeoSeries(potential_outposts.set_index('id')["geometry"]).to_json()

In [ ]:
create_choropleth_and_heatmap(potential_outposts, data_geo_1, ["id","ranks"], 'Outpost', 'counts', 5, table_people, ['lat', 'lon', 'count_people'])

In [ ]:
create_choropleth_and_heatmap(potential_outposts, data_geo_1, ["id","ranks"], 'Outpost', 'counts', 5, table_workers, ['lat', 'lon', 'count_workers'])

# Метод Personalized PageRank

Реализация: https://github.com/asajadi/fast-pagerank

Отличается от PageRank тем, что добавляется вектор предпочтений для вершин. В данном случае ставим большее предпочтение гексагонам с большим значением метрики, при этом сделаем возможным переход между всеми соседними гексагонами.

## Генерация матрицы переходов

In [ ]:
a = []

def get_hex_id(row):
    return h3.geo_to_h3(row['lat'], row['lon'], 8)

ids = {}
for idx, row in hex_features.iterrows():
    ids[row['id']] = get_hex_id(row)

for idx, row in hex_features.iterrows():
    line = []
    for idx2, row2 in hex_features.iterrows():
        are_neigh = h3.h3_indexes_are_neighbors(ids[row['id']], ids[row2['id']])
        line.append(int(are_neigh))
    a.append(line)

a = np.array(a)
a = sparse.csr_matrix(a)
a

<184x184 sparse matrix of type '<class 'numpy.longlong'>'
	with 864 stored elements in Compressed Sparse Row format>

In [ ]:
a.sum()

864

## Вычисление рангов гексагонов и нахождение индексов лучших из них

Для получения вектора предпочтительности гексагонов в виде вероятности, вычислим софтмакс от значений метрики. Чтобы избежать слишком сильного влияния больших значений, логарифмируем значения, а также добавляем к аргументу логарифма единицу, чтобы аргумент был строго больше нуля.

In [ ]:
personalize = hex_features['metric'].to_numpy()
personalize = torch.nn.functional.softmax(torch.from_numpy(np.log(personalize + 1)), dim=-1).numpy()

ranks = pagerank(a, p=0.85, personalize=personalize)
hex_features['personalized_ranks'] = ranks
indices = ranks.argsort()[-10:]
best_ids_3 = np.take(hex_features.id.tolist(), indices)
print(best_ids_3)
print(ranks[indices])

['48' '68' '85' '835' '443' '635' '354' '290' '23' '168']
[0.01024425 0.01041918 0.01047839 0.01054425 0.0106273  0.01083755
 0.01171867 0.01188316 0.01210592 0.01253093]


/usr/local/lib/python3.7/dist-packages/fast_pagerank/fast_pagerank.py:49: DeprecationWarning: scipy.asarray is deprecated and will be removed in SciPy 2.0.0, use numpy.asarray instead
  r = sp.asarray(A.sum(axis=1)).reshape(-1)


В таблице отображены гексагоны с самыми лучшими значениями в столбце personalized_ranks

In [ ]:
hex_features[hex_features.id.isin(best_ids_3)]

id        lat        lon  ...        metric     ranks  personalized_ranks
11   168  54.345053  48.388075  ...  10771.000000  0.012887            0.012531
29    23  54.320189  48.386178  ...   9118.000000  0.020849            0.012106
46   290  54.300144  48.319936  ...   9636.000000  0.011684            0.011883
62   354  54.336737  48.389536  ...   2993.000000  0.005667            0.011719
85   443  54.323435  48.399116  ...   4999.500000  0.008671            0.010627
93    48  54.310284  48.385564  ...   4575.666667  0.011663            0.010244
128  635  54.331761  48.399117  ...   6096.500000  0.007222            0.010838
138   68  54.311917  48.358385  ...   8460.000000  0.011988            0.010419
177  835  54.328238  48.388330  ...   3914.000000  0.015398            0.010544
178   85  54.283132  48.293655  ...   7050.000000  0.012437            0.010478

[10 rows x 9 columns]

## Отображение потенциальных мест для открытия ПВЗ
Шкала отображает предпочтение гексагонов, чем оно выше, тем предпочтительный гексагон.

In [ ]:
agg_all = agg_all.merge(hex_features[['id', 'personalized_ranks']], how='left', on='id')
potential_outposts = agg_all[agg_all.id.isin(best_ids_3)]

data_geo_1 = gpd.GeoSeries(potential_outposts.set_index('id')["geometry"]).to_json()

In [ ]:
create_choropleth_and_heatmap(potential_outposts, data_geo_1, ["id","personalized_ranks"], 'Outpost', 'counts', 5, table_people, ['lat', 'lon', 'count_people'])

In [ ]:
create_choropleth_and_heatmap(potential_outposts, data_geo_1, ["id","personalized_ranks"], 'Outpost', 'counts', 5, table_workers, ['lat', 'lon', 'count_workers'])

# Выводы

Сравнить методы не получится, так как информации об эффективности ПВЗ, расположенных в том или ином гексагоне нет (и вряд ли её выложат в открытый доступ такие компании, как Ozon или Wildberries, из-за опасений конкуренции).

На основе результатов можно сделать вывод, что выгоднее открыть ПВЗ на правобережье (на карте это левая часть города), причем там, где плотность населения наиболее высокая.

Подход в данном ноутбуке может использоваться и для других городов России, так как все города +- похожи в плане того, сколько человек живет в квартире и сколько людей работает в офисах. На других странах же этот подход может дать сбой, так как плотность населения в разных странах сильно отличается, например, в Индии и США.

# Как можно улучшить результаты?

1. Если провести более качественный анализ существующих построек в городе и найти сколько рабочих мест они создают, то можно более верно определить плотность рабочих мест.
2. Если всё-таки добиться данных об эффективности ПВЗ от Ozon и Wildberries, то можно научиться предсказывать эффективность ПВЗ в том или ином гексагоне.
3. Спарсить отзывы о существующих ПВЗ для того, чтобы выявить факты о том, что нравятся/не нравятся людям в ПВЗ, и на их основе сгенерировать дополнительные фичи.